In [1]:
import requests
import re
import folium
from geopy.geocoders import Nominatim
from geopy.point import Point
import json
import math

In [2]:
winterWeatherAdvisory_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=Winter%20Weather%20Advisory"
winterStormWarning_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=Winter%20Storm%20Warning"
winterStormWatch_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=Winter%20Storm%20Watch"
windAdvisory_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=Wind%20Advisory"
blizzardWarning_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=Blizzard%20Warning"
highWindWarning_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=High%20Wind%20Warning"
highWindWatch_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=High%20Wind%20Watch"
floodAdvisory_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=Flood%20Advisory"
floodWatch_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=Flood%20Watch"
floodWarning_URL = "https://forecast.weather.gov/wwamap/wwatxtget.php?cwa=cnrfc&wwa=Flood%20Warning"

In [3]:
def translateWeatherPage(URL):
    page = requests.get(URL)
    pageAsString = str(page.text)
    pieces = pageAsString.split("*")
    areas = []
    for i in pieces:
        if "WHERE..." in i:
            areas.append(re.sub(' +', ' ', i.split("WHERE...")[1]).strip())
    return areas

In [4]:
f = open('us-county-boundaries.json', 'r')
data = json.load(f)

In [5]:
def findCounties(URL):
    returnData = []
    for piece in translateWeatherPage(URL):
        for county in data:
            if county["namelsad"] in piece:
                returnData.append(county["namelsad"])
    return returnData

In [6]:
def mapOutWeather(URL, weight):
    listOfCounties = findCounties(URL)
    points_lat = []
    points_lng = []
    points = []
    
    for listedCounty in listOfCounties:
        for a in data:
            if listedCounty == a["namelsad"]:
                for i in a["geo_shape"]["geometry"]["coordinates"]:
                    if len(a["geo_shape"]["geometry"]["coordinates"]) > 1:
                        for b in i:
                            for lat, lon in b:
                                points_lat.append(lat)
                                points_lng.append(lon)
                                points.append([lon, lat])
                            if len(points) > 0:                    
                                folium.Polygon(points, color = 'red', weight = str(weight*5), 
                                               fill = True, fill_color = 'red', fill_opacity = weight).add_to(m)
                    else: 
                        for lat, lon in i:
                            points_lat.append(lat)
                            points_lng.append(lon)
                            points.append([lon, lat])
                        if len(points) > 0:                    
                                folium.Polygon(points, color = 'red', weight = str(weight), 
                                               fill = True, fill_color = 'red', fill_opacity = weight).add_to(m)
                    points = []

In [7]:
m = folium.Map(location=[37.45, -122], zoom_start=5)

mapOutWeather(winterWeatherAdvisory_URL, 0.1)
mapOutWeather(winterStormWatch_URL, 0.2)
mapOutWeather(winterStormWarning_URL, 0.15)
mapOutWeather(windAdvisory_URL, 0.2)
mapOutWeather(blizzardWarning_URL, 0.3)
mapOutWeather(highWindWarning_URL, 0.3)
mapOutWeather(highWindWatch_URL, 0.3)
mapOutWeather(floodAdvisory_URL, 0.1)
mapOutWeather(floodWatch_URL, 0.2)
mapOutWeather(floodWarning_URL, 0.2)
m

In [8]:
california_counties_population = {
    "Alameda": 1676753,
    "Alpine": 1129,
    "Amador": 40331,
    "Butte": 234417,
    "Calaveras": 45235,
    "Colusa": 21601,
    "Contra Costa": 1160919,
    "Del Norte": 28045,
    "El Dorado": 193582,
    "Fresno": 1005919,
    "Glenn": 28935,
    "Humboldt": 135311,
    "Imperial": 181215,
    "Inyo": 18803,
    "Kern": 905936,
    "Kings": 151506,
    "Lake": 64789,
    "Lassen": 29451,
    "Los Angeles": 10086284,
    "Madera": 162470,
    "Marin": 259943,
    "Mariposa": 17469,
    "Mendocino": 86324,
    "Merced": 274765,
    "Modoc": 8660,
    "Mono": 14825,
    "Monterey": 438513,
    "Napa": 139925,
    "Nevada": 100387,
    "Orange": 3172532,
    "Placer": 398329,
    "Plumas": 18441,
    "Riverside": 2499619,
    "Sacramento": 1565135,
    "San Benito": 63641,
    "San Bernardino": 2193936,
    "San Diego": 3338330,
    "San Francisco": 881549,
    "San Joaquin": 782458,
    "San Luis Obispo": 285719,
    "San Mateo": 778759,
    "Santa Barbara": 448230,
    "Santa Clara": 1942615,
    "Santa Cruz": 274255,
    "Shasta": 179422,
    "Sierra": 3150,
    "Siskiyou": 43045,
    "Solano": 448671,
    "Sonoma": 499772,
    "Stanislaus": 546191,
    "Sutter": 97531,
    "Tehama": 65647,
    "Trinity": 12298,
    "Tulare": 466721,
    "Tuolumne": 55554,
    "Ventura": 854223,
    "Yolo": 225774,
    "Yuba": 79463
}

In [9]:
p = folium.Map(location=[37.45, -122], zoom_start=5)
for area in california_counties_population:
    points_lat = []
    points_lng = []
    points = []
    for county in data:
        if area == county["name"]:
            for i in county["geo_shape"]["geometry"]["coordinates"]:
                if len(county["geo_shape"]["geometry"]["coordinates"]) > 1:
                    for b in i:
                        for lat, lon in b:
                            points_lat.append(lat)
                            points_lng.append(lon)
                            points.append([lon, lat])
                        if len(points) > 0:                    
                            folium.Polygon(points, color = 'black', weight = 0.5, 
                                            fill = True, fill_color = 'black', fill_opacity = california_counties_population[area]/2500000).add_to(p)
                else: 
                    for lat, lon in i:
                        points_lat.append(lat)
                        points_lng.append(lon)
                        points.append([lon, lat])
                    if len(points) > 0:                    
                            folium.Polygon(points, color = 'black', weight = 0.5, 
                                           fill = True, fill_color = 'black', fill_opacity = california_counties_population[area]/2500000).add_to(p)
                
                points = []
                
p